# Photo bleaching

This is an example to test the effect of photo bleaching.

In [1]:
import scopyon

Enable photo bleaching and set the half life of fluorophore.

In [2]:
config = scopyon.DefaultConfiguration()
config.update("""
default:
    magnification: 360
    detector:
        exposure_time: 0.033
    effects:
        photo_bleaching:
            switch: true
            half_life: 2.5
""")

In [3]:
pixel_length = config.default.detector.pixel_length / config.default.magnification
L_2 = config.default.detector.image_size[0] * pixel_length * 0.5

Set the number of processes to enable `multiprocessing`:

In [4]:
config.environ.processes = 20

Generate input data.

In [5]:
import numpy
rng = numpy.random.RandomState(123)
num_frames = 30
N = 1000
D = 0.1e-12  # m ** 2 / s
dt = config.default.detector.exposure_time
t = numpy.arange(0, (num_frames + 1) * dt, dt)
inputs = scopyon.sample_inputs(t, N=N, lower=-L_2, upper=+L_2, ndim=2, D=D, rng=rng)

Form images.

In [6]:
imgs = list(scopyon.generate_images(inputs, num_frames=num_frames, config=config, rng=rng))

Create a video (`matplotlib` and `ffmpeg` are required).

In [7]:
scopyon.Video.save('video.mp4', imgs)

In [8]:
from IPython.display import Video
Video("video.mp4", embed=True)

Plot the total intensity of images.

In [9]:
import plotly.express as px
px.line(x=numpy.arange(len(imgs)) * config.default.detector.exposure_time, y=[img.as_array().sum() for img in imgs])